In [229]:
import numpy as np
import pandas as pd
import pyomo.environ as pyo
from pyomo.opt import SolverFactory, TerminationCondition

import pandas as pd
from pyomo.util.infeasible import log_infeasible_constraints
import pandapower as pp
import scipy
from scipy.sparse import csr_matrix
import pypsa
import geopandas as gpd
import pp_create_basic_network as basic
import matplotlib.pyplot as plt

case_id='225-1_0_6'
zone='Midlands-Periurban'
MV_feeder = True
grid = "369_0"
folder ='225-1_0_6'#'298-6_0_2'#'298-4_1_5'#'216-1_1_3' 
scenario_year = 2050
weekday = "Friday"
day_start_ts = pd.to_datetime(f"{scenario_year}-01-07 00:00:00")
day_start = day_start_ts.day
day_end_ts = pd.to_datetime(f"{scenario_year}-01-08 00:00:00")
# month = day_start_ts.month
monitor_hr =int((day_end_ts - day_start_ts).total_seconds() / 3600)
path_controlled = f"{grid}/{scenario_year}_{weekday}_01_07_controlled"
path_uncontrolled = f"{grid}/{scenario_year}_{weekday}_01_07_uncontrolled"


In [230]:
net = pp.from_excel(f"{case_id}_{day_start_ts}.xlsx")
base_load_profile=pd.read_pickle(f"{case_id}_base_load_profile.pkl")
hp_load_profile=pd.read_pickle(f"{case_id}_hp_load_profile.pkl")
pv_load_profile = pd.read_pickle(f"{case_id}_pv_load_profile.pkl")
ev_load_profile = pd.read_pickle(f"{case_id}_ev_load_profile.pkl")


try:
    pp.runpp(net)
except pp.LoadflowNotConverged:
    print("Load flow did not converge.")   
coo_Ybus = net._ppc["internal"]["Ybus"].tocoo()
Ybus_g_dict = {(i, j): v for i, j, v in zip(coo_Ybus.row, coo_Ybus.col, coo_Ybus.data.real)}
Ybus_b_dict = {(i, j): v for i, j, v in zip(coo_Ybus.row, coo_Ybus.col, coo_Ybus.data.imag)}


branch_data = net._ppc['branch']
fbus = branch_data[:,0].astype(int)
tbus = branch_data[:,1].astype(int)
branch_ft_bus_tuple = list(zip(fbus,tbus))#+list(zip(tbus,fbus))

BRANCH_SMAX_trafo = dict(zip(list(zip(net.trafo.hv_bus,net.trafo.lv_bus)),net.trafo.sn_mva))
BRANCH_SMAX_line = dict(zip(list(zip(net.line.from_bus,net.line.to_bus)),net.line.max_i_ka * net.bus.loc[net.line.from_bus.values].vn_kv.values * np.sqrt(3)))
BRANCH_SMAX_line.update(BRANCH_SMAX_trafo)
# Base Load Data
base_PD_coo = scipy.sparse.coo_matrix(np.array(base_load_profile.p_mw.tolist()))
base_PD_dict = {(bus, t): v for bus, t, v in zip(base_PD_coo.row, base_PD_coo.col, base_PD_coo.data)}
base_PQ_coo = scipy.sparse.coo_matrix(np.array(base_load_profile.q_mvar.tolist()))
base_PQ_dict = {(bus, t): v for bus, t, v in zip(base_PQ_coo.row, base_PQ_coo.col, base_PQ_coo.data)}

# PV data
PV_to_BUS_dict = pv_load_profile.Bus.to_dict()
pv_bus_tuple =[(PV,int(BUS)) for PV,BUS in  PV_to_BUS_dict.items()]
PV_max_coo = scipy.sparse.coo_matrix(np.array(pv_load_profile.pv_P_daily.tolist())) # sparse matrix:row: pv index -> column: monitor_hr -> data: maximal PV power generation
PV_max_dict = {(pv,int(PV_to_BUS_dict[pv]),t): v for pv, t, v in zip(PV_max_coo.row, PV_max_coo.col, PV_max_coo.data)}

# HP Data
HP_PD_BUS = hp_load_profile.groupby('Bus').agg({'p':lambda x: np.sum(np.array(x.tolist()), axis=0),'q':lambda x: np.sum(np.array(x.tolist()), axis=0)})
hp_PD_coo = scipy.sparse.coo_matrix(np.array(HP_PD_BUS.p.tolist()))
hp_PQ_coo = scipy.sparse.coo_matrix(np.array(HP_PD_BUS.q.tolist()))
hp_PD_dict = {(bus, t): v for bus, t, v in zip(hp_PD_coo.row, hp_PD_coo.col, hp_PD_coo.data)}
hp_PQ_dict = {(bus, t): v for bus, t, v in zip(hp_PD_coo.row, hp_PQ_coo.col, hp_PQ_coo.data)}

# EV Data
PARK_to_EVBAT_dict = ev_load_profile.person.to_dict() # key: parking event -> value: person
PARK_to_BUS_dict = ev_load_profile.Bus.to_dict() # key: parking event -> vlaue: bus_id
PARK_to_ENDIDX_dict = ev_load_profile.park_end_time_idx.to_dict() # key:parking event -> value: park_end_time_idx
PARK_to_ARRIDX_dict = ev_load_profile.arr_time_idx.to_dict() # key:parking event -> value: arr_time_idx
park_bus_tuple = [(PARK,int(PARK_to_EVBAT_dict[PARK]),max(PARK_to_ARRIDX_dict[PARK],0),min(int(PARK_to_ENDIDX_dict[PARK]),monitor_hr-1),int(BUS)) for PARK,BUS in  PARK_to_BUS_dict.items()] # (Parking event person,arr_time_idx, park_end_time_idx, bus)

PARK_PD_coo = scipy.sparse.coo_matrix(ev_load_profile.optimized_power_list.tolist()) # sparse matrix:row: parking event -> column: monitor_hr -> data: origin charging power of battery in consumer system
PARK_PD_dict = {(PARK,int(PARK_to_EVBAT_dict[PARK]),max(PARK_to_ARRIDX_dict[PARK],0),min(int(PARK_to_ENDIDX_dict[PARK]),monitor_hr-1),int(PARK_to_BUS_dict[PARK]), t): -v for PARK, t, v in zip(PARK_PD_coo.row, PARK_PD_coo.col, PARK_PD_coo.data)} # key:(parking event,perosn,arr_time_idx,park_end_time_idx, bus_id, monitor_hr) -> value: ev battery injectied power from grid's perspective

PARKHR_coo = scipy.sparse.coo_matrix(ev_load_profile.hourly_time_dict.tolist()) 
PARKHR_dict = {(PARK,int(PARK_to_EVBAT_dict[PARK]),max(PARK_to_ARRIDX_dict[PARK],0),min(int(PARK_to_ENDIDX_dict[PARK]),monitor_hr-1), int(PARK_to_BUS_dict[PARK]),t):v/60 for PARK,t,v in zip(PARKHR_coo.row,PARKHR_coo.col,PARKHR_coo.data)} # key:(parking event,perosn,arr_time_idx,park_end_time_idx, bus_id, monitor_hr) -> value: parking duration in Hour for this hour

SOE_dayend_dict = (ev_load_profile[['person','day_end_soe']].groupby('person').last().day_end_soe/1e3).to_dict()

NEXT_E = ev_load_profile.next_travel_TP2_consumption/1e3
NEXT_E_dict =  {(PARK,int(PARK_to_EVBAT_dict[PARK]),max(PARK_to_ARRIDX_dict[PARK],0),min(int(PARK_to_ENDIDX_dict[PARK]),monitor_hr-1),int(PARK_to_BUS_dict[PARK])):next_e for PARK,next_e in zip(NEXT_E.index,NEXT_E.values)}
NEXT_2E = ev_load_profile.next_2_travel_TP2_consumption/1e3
NEXT_2E_dict =  {(PARK,int(PARK_to_EVBAT_dict[PARK]),max(PARK_to_ARRIDX_dict[PARK],0),min(int(PARK_to_ENDIDX_dict[PARK]),monitor_hr-1),int(PARK_to_BUS_dict[PARK])):next_2e for PARK,next_2e in zip(NEXT_2E.index,NEXT_2E.values)}
SOE_change = scipy.sparse.coo_matrix(np.array(ev_load_profile.SoE_change/1e3))
SOE_change_dict = {(PARK,int(PARK_to_EVBAT_dict[PARK]),max(PARK_to_ARRIDX_dict[PARK],0),min(int(PARK_to_ENDIDX_dict[PARK]),monitor_hr-1),int(PARK_to_BUS_dict[PARK])):soe_change for PARK, soe_change in zip(SOE_change.col,SOE_change.data)}

FIRST_PARKING = ev_load_profile[ev_load_profile.parking_cnt==0]
SOE_init_dict = dict(zip(FIRST_PARKING['person'],FIRST_PARKING['augmented_SoE_bc']/1e3))


# Merge Fixed Demand dicts (Base load + HP)
def merge_dicts(dict1,dict2):
    merged_dict = {}
    for key in set(dict1.keys()).union(dict2.keys()):
        merged_dict[key] = dict1.get(key, 0) + dict2.get(key, 0)
    return merged_dict
PD_dict = merge_dicts(base_PD_dict,hp_PD_dict)
PQ_dict = merge_dicts(base_PQ_dict,hp_PQ_dict)

numba cannot be imported and numba functions are disabled.
Probably the execution is slow.
Please install numba to gain a massive speedup.
(or if you prefer slow execution, set the flag numba=False to avoid this warning!)



Load flow did not converge.


/var/folders/xp/pv3t69qj4q11g2bjy5l0qfv40000gn/T/ipykernel_37953/2361426589.py:18: ComplexWarning:

Casting complex values to real discards the imaginary part

/var/folders/xp/pv3t69qj4q11g2bjy5l0qfv40000gn/T/ipykernel_37953/2361426589.py:19: ComplexWarning:

Casting complex values to real discards the imaginary part



In [231]:
def soe_init_rule(model, person,t):
    if t==0:
        return SOE_init_dict.get(person,0)
    else:
        return 0
def SOE_bound_rule(model, person, t):
    max_soe = FIRST_PARKING.loc[FIRST_PARKING.person == person, 'B'].values[0] / 1e3
    return (0, max_soe)

def PVGEN_bound_rule(model,pv,bus,t):
    return (0,PV_max_dict.get((pv,bus,t),0))

In [232]:
def EVGEN_bound_rule(model,ev,person,arr_idx,end_idx,bus,t):
    if ev_load_profile.loc[ev].hourly_time_dict[t]<=0:
        return(0,0)
    else:
        chg_rate_MW=ev_load_profile.loc[ev]['chg rate']/1e3
        return (-chg_rate_MW,chg_rate_MW)

In [233]:
def PBRANCH_bound_rule(model,fbus,tbus,t):
    return (-BRANCH_SMAX_line[(fbus,tbus)], BRANCH_SMAX_line[(fbus,tbus)])

In [239]:
m = pyo.ConcreteModel()
# Const:
slack=net._ppc['internal']['ref'][0]
# Sets
m.BUS =  pyo.Set(initialize = net.bus.index.values) # Bus Set
m.BUSPPC = pyo.Set(initialize = net._pd2ppc_lookups["bus"][net.bus.index.values]) # Internal Bus Set
m.BRANCH = pyo.Set(dimen=2,initialize=branch_ft_bus_tuple) # Branch Set including line and trafos [0]fbus,[1]tbus
m.EVBAT = pyo.Set(initialize=net.storage.person.unique()) # EV Set

m.PV = pyo.Set(dimen=2,initialize = pv_bus_tuple) # (PV, Bus) Set
m.PARK = pyo.Set(dimen=5,initialize=park_bus_tuple) # (Parking Event,EVBAT,Bus) Set

m.T = pyo.Set(initialize=range(24))

# Variables
m.PEXTGEN = pyo.Var(m.T,within=pyo.Reals,initialize=0) # External Generator
m.V = pyo.Var(m.BUS,m.T,within=pyo.Reals,bounds=(0.9,1.1),initialize=1) # Bus voltage magnitude in p.u.
m.ANG = pyo.Var(m.BUS,m.T,within=pyo.Reals,bounds=(-360,360),initialize=0) # Bus voltage angle 
m.PVGEN = pyo.Var(m.PV,m.T,within=pyo.NonNegativeReals, bounds=PVGEN_bound_rule,initialize=0)
m.EVGEN = pyo.Var(m.PARK,m.T,within=pyo.Reals,bounds=EVGEN_bound_rule,initialize=0)
m.PBRANCH = pyo.Var(m.BRANCH,m.T,within=pyo.Reals,bounds=PBRANCH_bound_rule,initialize=0)

m.SOE = pyo.Var(m.EVBAT,m.T,within=pyo.NonNegativeReals,bounds=SOE_bound_rule,initialize=soe_init_rule)

# Parameter
# m.YBUSG = pyo.Param(m.BUSPPC,m.BUSPPC,initialize=Ybus_g_dict,default=0)
m.YBUSB = pyo.Param(m.BUSPPC,m.BUSPPC,initialize=Ybus_b_dict,default=0)
m.PD = pyo.Param(m.BUS,m.T,initialize=PD_dict,default=0) # Fixed demand at each Bus
m.SOE_init = pyo.Param(m.EVBAT,initialize=SOE_init_dict)
m.EVPPLAN = pyo.Param(m.PARK,m.T,initialize=PARK_PD_dict,default=0) # Grid Perspecitve, positive P means discharging the battery
m.PARKHR = pyo.Param(m.PARK,m.T,initialize=PARKHR_dict,default=0) # Parking Duration in Hour for each parking event
m.SOE_dayend = pyo.Param(m.EVBAT,initialize=SOE_dayend_dict)
m.NEXT_2E = pyo.Param(m.PARK,initialize=NEXT_2E_dict) # Next trip's energy consumpiton
m.SOE_change = pyo.Param(m.PARK,initialize=SOE_change_dict,default=0)

In [240]:
def power_balance_rule(m,bus,t):
    gen_power = (
        sum(m.PVGEN[pv,bus,t] for pv,b in m.PV if b==bus) + 
        sum(m.EVGEN[park,ev,arr_idx,end_idx,bus,t] for park,ev,arr_idx,end_idx,b in m.PARK if b==bus) +
        (m.PEXTGEN[t] if bus==slack else 0)
    )
    load_power = m.PD[bus,t]
    net_power_injection = gen_power - load_power
    incoming_flow = sum(m.PBRANCH[i,j,t] for i, j in m.BRANCH if j==bus)
    outgoing_flow = sum(m.PBRANCH[i,j,t] for i, j in m.BRANCH if i==bus)
    return net_power_injection == outgoing_flow-incoming_flow
m.PowerBalance = pyo.Constraint(m.BUS,m.T,rule=power_balance_rule)

def slack_bus_rule(m,t):
    return m.ANG[slack,t]==0
m.SlackBus = pyo.Constraint(m.T,rule=slack_bus_rule)

def branch_flow_rule(m,i,j,t):
    return m.PBRANCH[i,j,t]==m.YBUSB[i,j]*(m.ANG[i,t]-m.ANG[j,t])
m.BranchFlow = pyo.Constraint(m.BRANCH,m.T,rule=branch_flow_rule)

def soe_agg_dynamic_rule(m,person,t):
    #m.SOE represent the SOE status at the end of current hour t
    if t==0:
        return m.SOE[person,0]==m.SOE_init[person]+sum(-m.EVGEN[park,ev,arr_idx,end_idx,bus,0]*m.PARKHR[park,ev,arr_idx,end_idx,bus,0] for park,ev,arr_idx,end_idx,bus in m.PARK if ev==person)
    return m.SOE[person,t] == (
                                m.SOE[person,t-1]+
                                sum(-m.EVGEN[park,ev,arr_idx,end_idx,bus,t]*m.PARKHR[park,ev,arr_idx,end_idx,bus,t] for park,ev,arr_idx,end_idx,bus in m.PARK if ev==person)-
                                sum(-m.SOE_change[park,ev,arr_idx,end_idx,bus] for park,ev,arr_idx,end_idx,bus in m.PARK if (ev==person and t==arr_idx))
                            )
m.SoeAggDynamics = pyo.Constraint(m.EVBAT,m.T,rule=soe_agg_dynamic_rule)

def soe_next_trip_rule(m,park,ev,arr_idx,end_idx,bus,t):
    if end_idx==t:
        return m.SOE[ev,t]>=m.NEXT_2E[park,ev,arr_idx,end_idx,bus]
    else:
        return pyo.Constraint.Skip
m.SoeNextTrip = pyo.Constraint(m.PARK,m.T,rule=soe_next_trip_rule)

# def day_end_soe_rule(m,person):
#         return m.SOE[person,monitor_hr-1]>=m.SOE_dayend[person]
# m.SoeDayEnd = pyo.Constraint(m.EVBAT,rule=day_end_soe_rule)

# def objective_rule(m):
#     """
#     Maximize PV Power Injection to the Grid
#     """
#     return sum(-m.PVGEN[pv,bus,t] for pv,bus in m.PV for t in m.T)

def objective_rule(m):
    """
    Minimize day end SOE difference
    """
    return sum(m.SOE_dayend[person] - m.SOE[person,monitor_hr-1] for person in m.EVBAT)

m.OBJ = pyo.Objective(rule=objective_rule,sense=pyo.minimize)

# Solve the model
solver = pyo.SolverFactory('gurobi')
results = solver.solve(m, tee=True)


# Check for infeasibility
if results.solver.termination_condition == TerminationCondition.infeasible:
    print("The model is infeasible")
    
    # Identify and print infeasible constraints
    # Relax each constraint one by one and check feasibility
    for c in m.component_objects(pyo.Constraint, active=True):
        c.deactivate()
        results = solver.solve(m, tee=False)
        if results.solver.termination_condition != TerminationCondition.infeasible:
            print(f"Constraint {c.name} is causing infeasibility")
        c.activate()
else:
    print("The model is feasible")
    # Optional: Print solution values
    m.display()

# Optional: Print detailed solver status
print("Solver Status: ", results.solver.status)
print("Solver Termination Condition: ", results.solver.termination_condition)

Set parameter Username
Academic license - for non-commercial use only - expires 2025-02-19
Read LP format model from file /var/folders/xp/pv3t69qj4q11g2bjy5l0qfv40000gn/T/tmpmh2qu059.pyomo.lp
Reading time = 0.03 seconds
x1: 17122 rows, 26521 columns, 51446 nonzeros
Gurobi Optimizer version 11.0.0 build v11.0.0rc2 (mac64[arm] - Darwin 23.3.0 23D60)

CPU model: Apple M1 Pro
Thread count: 8 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 17122 rows, 26521 columns and 51446 nonzeros
Model fingerprint: 0x26d2e972
Coefficient statistics:
  Matrix range     [2e-02, 2e+04]
  Objective range  [1e+00, 8e+00]
  Bounds range     [2e-08, 4e+02]
  RHS range        [5e-05, 1e-01]
Presolve removed 13166 rows and 20730 columns
Presolve time: 0.02s
Presolved: 3956 rows, 5791 columns, 14543 nonzeros

Concurrent LP optimizer: primal simplex, dual simplex, and barrier
Showing barrier log only...

Ordering time: 0.01s

Barrier statistics:
 AA' NZ     : 1.335e+04
 Factor NZ

In [202]:
soe_data = {(person, t): pyo.value(m.SOE[person, t]) for person in m.EVBAT for t in m.T}
soe_df = pd.DataFrame.from_dict(soe_data, orient='index', columns=['SOE'])
# Reset the index to have 'person' and 'time' as columns
soe_df.index = pd.MultiIndex.from_tuples(soe_df.index, names=['person', 'time'])
# Unstack the DataFrame to make 'time' the columns and 'person' the index
soe_df = soe_df.unstack(level='time')
# The 'unstack' operation creates a multi-level column, so we flatten it
soe_df.columns = soe_df.columns.get_level_values(1)

In [ ]:
# Day end soe change
plt.boxplot((soe_df[23]-pd.Series(SOE_dayend_dict)).values)

In [153]:
EVGEN_data = {(park,t):pyo.value(-m.EVGEN[park,person,arr_idx,end_idx,bus,t]) for (park,person,arr_idx,end_idx,bus) in m.PARK for t in m.T}
EVGEN_df = pd.DataFrame.from_dict(EVGEN_data, orient='index', columns=['EVGEN'])
EVGEN_df.index = pd.MultiIndex.from_tuples(EVGEN_df.index,names=['park','time'])
EVGEN_df = EVGEN_df.unstack(level='park')
EVGEN_df.columns = EVGEN_df.columns.get_level_values(1)

In [91]:
PVGEN_data = {(pv,t):pyo.value(m.PVGEN[pv,bus,t]) for (pv,bus) in m.PV for t in m.T}
PVGEN_df = pd.DataFrame.from_dict(PVGEN_data, orient='index', columns=['PVGEN'])
PVGEN_df.index = pd.MultiIndex.from_tuples(PVGEN_df.index,names=['pv','time'])
PVGEN_df = PVGEN_df.unstack(level='pv')
PVGEN_df.columns = PVGEN_df.columns.get_level_values(1)
PVGENMAX = pd.DataFrame(pv_load_profile.pv_P_daily.tolist()).T

In [102]:
base_p = pd.DataFrame(base_load_profile.p_mw).T.apply(pd.Series.explode).reset_index(drop=True)
base_q = pd.DataFrame(base_load_profile.q_mvar).T.apply(pd.Series.explode).reset_index(drop=True)
hp_p = pd.DataFrame(hp_load_profile.p).T.apply(pd.Series.explode).reset_index(drop=True)
hp_q = pd.DataFrame(hp_load_profile.q).T.apply(pd.Series.explode).reset_index(drop=True)

In [ ]:
for t in range(24):
    net.load.loc[net.load.category == 'base', 'p_mw'] = base_p.loc[t].values
    net.load.loc[net.load.category=='base','q_mvar'] = base_q.loc[t].values
    net.load.loc[net.load.category == 'hp', 'p_mw'] = hp_p.loc[t].values
    net.load.loc[net.load.category == 'hp', 'q_mvar'] = hp_q.loc[t].values
    net.sgen.loc[net.sgen.type=='PV','p_mw'] = PVGEN_df.loc[t].values
    net.sgen.loc[net.sgen.type=='PV','q_mvar'] = PVGEN_df.loc[t].values*np.tan(np.arccos(0.97))
    net.storage.loc[net.storage.type=='ev','p_mw'] = EVGEN_df.loc[t].values
    pp.runpp(net)
    plt.figure(figsize=(6,6))
    plt.boxplot(net.res_bus.vm_pu)

    plt.figure(figsize=(6,6))
    plt.boxplot(net.res_line.loading_percent)